In [ ]:
# mount drive
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
# update working directory
import sys
sys.path.append('/content/drive/MyDrive/Colab Notebooks/Licenta/SAM-DeepfakeLocalization-local')

In [ ]:
!pip install tensorboardX
!pip install torchmetrics
!{sys.executable} -m pip install 'git+https://github.com/facebookresearch/sam2.git' # colab

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.7/101.7 kB 11.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 961.5/961.5 kB 53.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 3.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 100.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 95.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 60.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 41.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 19.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 4.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 108.5 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitli

In [ ]:
import os
import time
import torch.multiprocessing
from copy import deepcopy
from tqdm import tqdm
import shutil

from parameters import Parameters
from train.trainer import Trainer
from deepfake_datasets.datasets import get_dataloader
from train.early_stopping import EarlyStopping
from train.validate import validate_detection, validate_fully_supervised_localization
from utils.utils import compute_mean_iou, compute_mean_ap, compute_mean_f1, compute_mean_acc_detection, compute_mean_ap_detection, compute_batch_iou, compute_batch_localization_f1, compute_batch_ap, compute_accuracy_detection, compute_average_precision_detection

In [ ]:
!mkdir -p ../checkpoints/
!wget -P ../checkpoints/ https://dl.fbaipublicfiles.com/segment_anything_2/092824/sam2.1_hiera_small.pt

--2025-04-30 18:05:36--  https://dl.fbaipublicfiles.com/segment_anything_2/092824/sam2.1_hiera_small.pt
Resolving dl.fbaipublicfiles.com (dl.fbaipublicfiles.com)... 108.157.254.124, 108.157.254.121, 108.157.254.102, ...
Connecting to dl.fbaipublicfiles.com (dl.fbaipublicfiles.com)|108.157.254.124|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 184416285 (176M) [application/vnd.snesdev-page-table]
Saving to: ‘../checkpoints/sam2.1_hiera_small.pt’

sam2.1_hiera_small. 100%[===================>] 175.87M   111MB/s    in 1.6s    

2025-04-30 18:05:38 (111 MB/s) - ‘../checkpoints/sam2.1_hiera_small.pt’ saved [184416285/184416285]



In [ ]:
torch.multiprocessing.set_sharing_strategy('file_system')

In [ ]:
new_dataset_name = 'pluralistic'

zip_path = f'/content/drive/MyDrive/Colab Notebooks/Licenta/DeCLIP-main/datasets_zip/{new_dataset_name}.zip'
new_content_root_path = f'/content/datasets/dolos_data/celebahq/fake/'

os.makedirs(new_content_root_path, exist_ok=True)

# move the dataset from drive to /content (SSD) for better performance in I/O
import zipfile
with zipfile.ZipFile(zip_path, 'r') as zip_ref:
    zip_ref.extractall(new_content_root_path)

In [ ]:
# set parameters
params = Parameters()

# set experiment name
params.experiment_name = 'first_try_training_sam_conv4'

params.arch = 'SAM'

# create output dirs
params.create_output_dirs()

new_root_path = '/content/datasets/dolos_data/celebahq/'
# new_root_path = 'D:\\Python\\DeCLIP-main\\datasets\\dolos_data\\celebahq\\'
new_dataset_name = 'pluralistic'

params.update_dolos_data_paths(new_root_path, new_dataset_name)

# fix the backbone - to train only the decoder
params.fix_backbone = True

# set SAM2 checkpoint and config paths
# params.sam_checkpoint_path = '/content/drive/MyDrive/Colab Notebooks/Licenta/SAM-DeepfakeLocalization-local/models/sam_checkpoints/sam2.1_hiera_large.pt'
#params.sam_config_path = '/content/drive/MyDrive/Colab Notebooks/Licenta/SAM-DeepfakeLocalization-local/models/sam_configs/sam2.1_hiera_l.yaml'
params.sam_checkpoint_path = '../checkpoints/sam2.1_hiera_small.pt'
params.sam_config_path = 'configs/sam2.1/sam2.1_hiera_s.yaml'


# set the feature layer and the decoder type
params.feature_layer = 'high_res_feats_0'
params.decoder_type = 'conv-20'

# set the batch size and num threads
params.batch_size = 32 # batch size 64 results in cuda error for some reason
params.num_threads = 4

# set the number of epochs
params.num_iter = 20

# loss type
params.loss_type = 'bce'

for key, value in params.__dict__.items():
    print(f"{key}: {value}")

experiment_name: first_try_training_sam_conv4
task_type: fully_supervised_localization
data_label: train
arch: CLIP:ViT-L/14
fix_backbone: True
sam_checkpoint_path: ../checkpoints/sam2.1_hiera_small.pt
sam_config_path: configs/sam2.1/sam2.1_hiera_s.yaml
weight_decay: 0.0
batch_size: 32
num_threads: 4
init_type: normal
init_gain: 0.02
train_dataset: pluralistic
decoder_type: conv-20
feature_layer: high_res_feats_0
early_stop_epochs: 5
optim: adam
beta1: 0.9
lr: 0.001
show_loss_freq: 50
num_iter: 20
data_root_path: /content/datasets/dolos_data/celebahq
train_fake_path: /content/datasets/dolos_data/celebahq/fake/pluralistic/images/train
valid_fake_path: /content/datasets/dolos_data/celebahq/fake/pluralistic/images/valid
test_fake_path: /content/datasets/dolos_data/celebahq/fake/pluralistic/images/test
train_masks_ground_truth_path: /content/datasets/dolos_data/celebahq/fake/pluralistic/masks/train
valid_masks_ground_truth_path: /content/datasets/dolos_data/celebahq/fake/pluralistic/masks/

In [ ]:
# get the model, along with its trainer
model_trainer = Trainer(params)

In [ ]:
# get the dataloaders
train_loader = get_dataloader(params)

val_params = deepcopy(params)
val_params.data_label = 'valid'
val_loader = get_dataloader(val_params)

In [ ]:
# start the training loop
model_trainer.model.verbose = False
# model_trainer.compute_pos_weight_per_dataset(train_loader)
early_stopping = EarlyStopping(patience=params.early_stop_epochs, verbose=True, delta=-0.001)
best_metric = 0.0 # iou for localization, ap for detection
print('Length of training set:', len(train_loader.dataset))
print('Length of validation set:', len(val_loader.dataset))
start_time = time.time()
for epoch in tqdm(range(params.num_iter)):
    print('Epoch:', epoch)

    epoch_loss = 0
    for data in train_loader:
        model_trainer.total_steps += 1

        if model_trainer.total_steps % params.show_loss_freq == 0:
            # model_trainer.model.verbose = True
            print('IOUs: ', model_trainer.ious)
        else:
            model_trainer.model.verbose = False

        model_trainer.set_input(data)
        model_trainer.optimize_parameters()

        if model_trainer.total_steps % params.show_loss_freq == 0:
            epoch_loss += model_trainer.loss.item()
            print(f'Train Loss: {model_trainer.loss.item():.4f} at step {model_trainer.total_steps} \t Iter time: {(time.time() - start_time) / model_trainer.total_steps:.2f}')


    epoch_loss /= len(train_loader.dataset)
    print(f'Average Train Loss: {epoch_loss:.4f}')

    # compute training metrics
    if params.task_type == 'fully_supervised_localization':
        compute_mean_iou(model_trainer.ious, verbose=True, extra_text=f'Train epoch {epoch} ')
        model_trainer.ious = []

        compute_mean_f1(model_trainer.f1_best, model_trainer.f1_fixed, verbose=True, extra_text=f'Train epoch {epoch} ')
        model_trainer.f1_best = []
        model_trainer.f1_fixed = []

        compute_mean_ap(model_trainer.ap, verbose=True, extra_text=f'Train epoch {epoch} ')
        model_trainer.ap = []


    # validate the model
    print('Validation:')
    if params.task_type == 'fully_supervised_localization':
        ious, f1_best, f1_fixed, mean_ap, _ = validate_fully_supervised_localization(model_trainer.model, val_loader, params.train_dataset)

        # compute metrics
        mean_iou = compute_mean_iou(ious, verbose=True, extra_text=f'Validation at epoch {epoch} ')

        mean_f1_best, mean_f1_fixed = compute_mean_f1(f1_best, f1_fixed, verbose=True, extra_text=f'Validation at epoch {epoch} ')

        mean_ap = compute_mean_ap(mean_ap, verbose=True, extra_text=f'Validation at epoch {epoch} ')

        # save the model if the mean iou is improved
        if mean_iou > best_metric:
            best_metric = mean_iou
            model_trainer.save_model(f'best_localization_model_iou_{mean_iou:.4f}.pth')
            print(f'Best model saved at epoch {epoch}!')

        # check for early stopping
        early_stopping(mean_iou)

    # check if early stopping is triggered
    if early_stopping.early_stop:
        print("Early stopping triggered")
        continue_training = model_trainer.adjust_learning_rate()
        if continue_training:
            print("Continuing training with a learning rate reduced by a factor of 10")
            early_stopping = EarlyStopping(patience=params.early_stop_epochs, verbose=True, delta=-0.002) # adjust the delta only once, otherwise stop completely
        else:
            print(f"Early stopping training at epoch {epoch}")
            break
    print()

Length of training set: 9000
Length of validation set: 900


  0%|          | 0/20 [00:00<?, ?it/s]

Epoch: 0
IOUs:  [4.435908421874046, 1.9988667219877243, 19.75591629743576, 4.8891812562942505, 5.7271406054496765, 1.6530217602849007, 4.590431600809097, 3.044012375175953, 16.210490465164185, 5.681775510311127, 20.925959944725037, 27.139854431152344, 25.766178965568542, 4.028860107064247, 2.1213894709944725, 0.4092638846486807, 18.23344975709915, 12.059695273637772, 5.219987779855728, 24.989882111549377, 27.957630157470703, 19.29064393043518, 1.3007252477109432, 1.9930984824895859, 26.24061405658722, 3.687504306435585, 4.530952125787735, 20.478862524032593, 4.380868002772331, 0.8479776792228222, 24.852432310581207, 3.0682848766446114, 8.160904049873352, 3.529290482401848, 17.64925867319107, 14.026211202144623, 0.5191109143197536, 3.895358368754387, 0.4244659561663866, 34.46744978427887, 8.772101998329163, 11.554502695798874, 36.98634207248688, 47.91033864021301, 5.2399639040231705, 3.2944239675998688, 34.88011956214905, 26.601219177246094, 3.4347064793109894, 3.757225349545479, 2.2171


100%|██████████| 29/29 [01:22<00:00,  2.86s/it]


Validation at epoch 0 Mean IOU: 44.34
Validation at epoch 0 Mean F1 best: 0.6578
Validation at epoch 0 Mean F1 fixed: 0.5658
Validation at epoch 0 Mean AP: 0.7114


...

Validation at epoch 18 Mean IOU: 90.74
Validation at epoch 18 Mean F1 best: 0.9389
Validation at epoch 18 Mean F1 fixed: 0.9143
Validation at epoch 18 Mean AP: 0.9839
Early Stopping counter: 1 out of 5

Epoch: 19
IOUs:  [86.82223558425903, 92.96916127204895, 96.58421277999878, 96.670001745224, 93.63740682601929, 93.02172660827637, 93.47553253173828, 95.78534960746765, 98.39653968811035, 97.0923662185669, 75.87354183197021, 98.42862486839294, 82.28621482849121, 97.57195711135864, 97.61479496955872, 87.28682398796082, 93.098384141922, 91.09442234039307, 94.46808695793152, 94.18094754219055, 96.15528583526611, 97.15655446052551, 95.8055317401886, 85.70241332054138, 87.56183981895447, 93.77431869506836, 91.74112677574158, 68.38235259056091, 98.32659959793091, 97.76808619499207, 98.28964471817017, 96.54515981674194, 90.48959016799927, 96.3528573513031, 96.67815566062927, 97.98076152801514, 98.01076054573059, 91.32820963859558, 88.47222328186035, 96.87727093696594, 91.17112159729004, 93.3713


100%|██████████| 29/29 [01:21<00:00,  2.81s/it]


Validation at epoch 19 Mean IOU: 91.25
Validation at epoch 19 Mean F1 best: 0.9487
Validation at epoch 19 Mean F1 fixed: 0.9362
Validation at epoch 19 Mean AP: 0.9847


100%|██████████| 20/20 [5:35:40<00:00, 1007.05s/it]

Best model saved at epoch 19!



In [ ]:
# model_trainer.save_model(f'best_localization_model_last_epoch_{epoch}.pth')

In [ ]:
from google.colab import files
model_dir = '/content/experiments/first_try_training_sam_conv4/models/'
model_files = sorted(
    [f for f in os.listdir(model_dir) if f.endswith('.pth')]
)

best_model = model_files[-1]
best_model_path = os.path.join(model_dir, best_model)

files.download(best_model_path)

In [ ]:
time.sleep(60)